In [17]:
import pandas as pd

# Path to your Excel file
file_path = 'Bicycle.xlsx'

# Read the 'ID' sheet and force all columns to string
id_df = pd.read_excel(file_path, sheet_name='ID', dtype=str)

# Convert all elements to string and fill NaNs (empty cells) with empty string
id_df = id_df.fillna('').astype(str)

# Optional: Display the DataFrame to verify
print(id_df.head())



  Model number Brakes Wheels Frame size Groupset Suspension Color
0        CITY-      R     26          S      SH1          -    01
1                   D     27          M      SH2          C    02
2                         29          L      SH3          A    03
3                                            SH4               04
4                                            SR1               05


In [23]:
type(id_df['Color'][0])

str

In [27]:
def non_empty_unique(col):
    return [v for v in col.unique() if v != '' and pd.notna(v)]

model_numbers = non_empty_unique(id_df['Model number'])
brakes        = non_empty_unique(id_df['Brakes'])
wheels        = non_empty_unique(id_df['Wheels'])
frame_sizes   = non_empty_unique(id_df['Frame size'])
groupsets     = non_empty_unique(id_df['Groupset'])
suspensions   = non_empty_unique(id_df['Suspension'])
colors        = non_empty_unique(id_df['Color'])


In [28]:
model_numbers

['CITY-']

In [30]:
import itertools
all_combinations = list(itertools.product(
    model_numbers,
    brakes,
    wheels,
    frame_sizes,
    groupsets,
    suspensions,
    colors
))

In [33]:
type(all_combinations[0])

tuple

In [34]:
combinations_as_strings = [
    tuple(str(element) for element in combo) for combo in all_combinations
]


In [36]:
for combo in combinations_as_strings[:5]:
    print(combo)
    

('CITY-', 'R', '26', 'S', 'SH1', '-', '01')
('CITY-', 'R', '26', 'S', 'SH1', '-', '02')
('CITY-', 'R', '26', 'S', 'SH1', '-', '03')
('CITY-', 'R', '26', 'S', 'SH1', '-', '04')
('CITY-', 'R', '26', 'S', 'SH1', '-', '05')


In [37]:
general_df = pd.read_excel(file_path, sheet_name='GENERAL', dtype=str)
brake_df   = pd.read_excel(file_path, sheet_name='1', dtype=str)
wheel_df   = pd.read_excel(file_path, sheet_name='2', dtype=str)
frame_df   = pd.read_excel(file_path, sheet_name='3', dtype=str)
group_df   = pd.read_excel(file_path, sheet_name='4', dtype=str)
susp_df    = pd.read_excel(file_path, sheet_name='5', dtype=str)
color_df   = pd.read_excel(file_path, sheet_name='6', dtype=str)


In [38]:
brake_lookup   = brake_df.set_index('Brakes').to_dict(orient='index')
wheel_lookup   = wheel_df.set_index('Wheels').to_dict(orient='index')
frame_lookup   = frame_df.set_index('Frame size').to_dict(orient='index')
group_lookup   = group_df.set_index('Groupset').to_dict(orient='index')
susp_lookup    = susp_df.set_index('Suspension').to_dict(orient='index')
color_lookup   = color_df.set_index('Color').to_dict(orient='index')
general_fields = general_df.iloc[0].to_dict()


In [39]:
import json

bikes = []
for combo in combinations_as_strings:
    model, brake, wheel, frame, group, susp, color = combo

    # Build the ID
    color_padded = color.zfill(2)
    id_str = f"{model}{brake}{wheel}{frame}{group}{susp}{color_padded}"

    # Look up attributes
    bike = {
        "ID": id_str,
        **general_fields,
        **brake_lookup[brake],
        **wheel_lookup[wheel],
        **frame_lookup[frame],
        **group_lookup[group],
        **susp_lookup[susp],
        **color_lookup[color],
    }

    # Convert boolean-like fields to TRUE/FALSE strings
    if 'Has suspension' in bike:
        bike['Has suspension'] = "TRUE" if bike['Has suspension'] == "1" else "FALSE"
    if 'Logo' in bike:
        bike['Logo'] = "TRUE" if bike['Logo'] == "1" else "FALSE"

    bikes.append(bike)


In [40]:
json_output = json.dumps(bikes, indent=4, ensure_ascii=False)
print(json_output)


[
    {
        "ID": "CITY-R26SSH1-01",
        "Manufacturer": "Bikes INC",
        "Type": "City",
        "Frame type": "Diamond",
        "Frame material": "Aluminum",
        "Brake type": "Rim",
        "Brake warranty": "2 years",
        "Operating temperature": "0 - 40 °C",
        "Wheel diameter": "26″",
        "Recommended height": "168-174 cm",
        "Frame height": "16 in",
        "Groupset manufacturer": "Shimano",
        "Groupset name": "Acera",
        "Gears": "27",
        "Has suspension": "FALSE",
        "Suspension travel": "Not applicable",
        "Frame color": "RED",
        "Logo": "FALSE"
    },
    {
        "ID": "CITY-R26SSH1-02",
        "Manufacturer": "Bikes INC",
        "Type": "City",
        "Frame type": "Diamond",
        "Frame material": "Aluminum",
        "Brake type": "Rim",
        "Brake warranty": "2 years",
        "Operating temperature": "0 - 40 °C",
        "Wheel diameter": "26″",
        "Recommended height": "168-174 cm",
 

In [42]:
len(bikes)

5508